In [ ]:
import pandas as pd
import numpy as np

# ---------------------------
# Load dimension CSVs
# ---------------------------
date_dim = pd.read_csv("date_dim.csv")       
client_dim = pd.read_csv("client_dim.csv")   
channel_dim = pd.read_csv("channel_dim.csv")
campaign_dim = pd.read_csv("campaign_dim.csv")  
fund_dim = pd.read_csv("fund_dim.csv")       

# ---------------------------
# Parameters for variability
# ---------------------------
CLIENT_RESP_PROB = 0.3   # probability a client interacts with a campaign on a day
FUND_RESP_PROB = 0.6     # probability a fund is included for that client on that day
NO_AUM_PROB = 0.4        # probability no AUM inflow occurs
NO_SIGNUPS_PROB = 0.5    # probability no new signups

# ---------------------------
# Helper function to generate metrics
# ---------------------------
def generate_metrics(client_au, channel_type):
    # Impressions
    impressions = np.random.randint(1000, 10000)
    
    # Click rate based on channel type
    if channel_type == "Paid":
        click_rate = np.random.uniform(0.03, 0.06)
    else:
        click_rate = np.random.uniform(0.01, 0.03)
    clicks = int(impressions * click_rate)
    
    leads = int(clicks * np.random.uniform(0.1, 0.15))
    new_signups = int(leads * np.random.uniform(0.3, 0.5))
    
    # Randomly zero out some AUM and signups
    aum = 0 if np.random.rand() < NO_AUM_PROB else int(client_au * np.random.uniform(0.002, 0.005))
    if np.random.rand() < NO_SIGNUPS_PROB:
        new_signups = 0
    
    weight = round(np.random.uniform(0.05, 0.5), 2)
    price_usd = round(np.random.uniform(20, 80), 2)
    
    return impressions, clicks, leads, new_signups, aum, weight, price_usd

# ---------------------------
# Generate GTM Fact Table
# ---------------------------
rows = []
id_counter = 1

for _, date_row in date_dim.head(20).iterrows():
    date_id = date_row['id']
    print('handling date row:', date_id)
    
    # Active campaigns for this date
    active_campaigns = campaign_dim[
        (pd.to_datetime(campaign_dim['start_date']) <= pd.to_datetime(date_row['date'])) &
        (pd.to_datetime(campaign_dim['end_date']) >= pd.to_datetime(date_row['date']))
    ]
    
    for _, campaign_row in active_campaigns.iterrows():
        print('handling campaign:', date_id, campaign_row['id'])
        campaign_id = campaign_row['id']
        channel_id = campaign_row['channel_id']
        channel_type = channel_dim.loc[channel_dim['id']==channel_id, 'channel_type'].values[0]
        
        # Randomly select a subset of clients for this campaign on this day
        num_clients = np.random.randint(0, len(client_dim)+1)
        selected_clients = client_dim.sample(n=num_clients) if num_clients > 0 else pd.DataFrame(columns=client_dim.columns)
        for _, client_row in selected_clients.iterrows():
            print('handling client:', date_id, campaign_row['id'], client_row['id'])
            client_id = client_row['id']
            client_au = client_row['total_assets_under_management']
            
            # Randomly select a subset of funds for this client/campaign/day
            num_funds = np.random.randint(0, len(fund_dim)+1)
            selected_funds = fund_dim.sample(n=num_funds) if num_funds > 0 else pd.DataFrame(columns=fund_dim.columns)
            for _, fund_row in selected_funds.iterrows():
                print('handling fund:', date_id, campaign_row['id'], client_row['id'], fund_row['id'])
                fund_id = fund_row['id']
                
                impressions, clicks, leads, new_signups, aum, weight, price_usd = generate_metrics(client_au, channel_type)
                
                rows.append([
                    id_counter, date_id, client_id, campaign_id, fund_id,
                    impressions, clicks, leads, new_signups,
                    aum, weight, price_usd
                ])
                id_counter += 1

gtm_fact = pd.DataFrame(rows, columns=[
    'id','date_id','client_id','campaign_id','fund_id',
    'impressions','clicks','leads','new_signups',
    'assets_under_management','weight','price_usd'
])

# ---------------------------
# Export to CSV
# ---------------------------
gtm_fact.to_csv("gtm_fact_realistic.csv", index=False)
print("gtm_fact_realistic.csv generated with", len(gtm_fact), "rows")


handling date row: 1
handling campaign: 1 1
handling client: 1 1 166
handling fund: 1 1 166 1
handling fund: 1 1 166 2
handling fund: 1 1 166 3
handling fund: 1 1 166 7
handling fund: 1 1 166 8
handling fund: 1 1 166 10
handling fund: 1 1 166 12
handling fund: 1 1 166 14
handling fund: 1 1 166 16
handling fund: 1 1 166 22
handling client: 1 1 146
handling fund: 1 1 146 2
handling fund: 1 1 146 4
handling fund: 1 1 146 10
handling fund: 1 1 146 12
handling fund: 1 1 146 13
handling fund: 1 1 146 15
handling fund: 1 1 146 18
handling fund: 1 1 146 19
handling fund: 1 1 146 20
handling fund: 1 1 146 21
handling client: 1 1 149
handling fund: 1 1 149 1
handling fund: 1 1 149 2
handling fund: 1 1 149 3
handling fund: 1 1 149 4
handling fund: 1 1 149 5
handling fund: 1 1 149 6
handling fund: 1 1 149 7
handling fund: 1 1 149 8
handling fund: 1 1 149 10
handling fund: 1 1 149 13
handling fund: 1 1 149 19
handling fund: 1 1 149 21
handling fund: 1 1 149 22
handling client: 1 1 115
handling fund

In [12]:
print(gtm_fact.head(10))

   id  date_id  client_id  campaign_id  fund_id  impressions  clicks  leads  \
0   1        1          1            1        1         4973     157     17   
1   2        1          1            1        2         6086     216     28   
2   3        1          1            1        3         4972     114     14   
3   4        1          1            1        4         6264     279     41   
4   5        1          1            1        5         8904     387     42   
5   6        1          1            1        6         7235     167     19   
6   7        1          1            1        7         6239     216     23   
7   8        1          1            1        8         7842     311     38   
8   9        1          1            1        9         4083     133     15   
9  10        1          1            1       10         5783     273     28   

   new_signups  assets_under_management  weight  price_usd  
0            7                 313606.0    0.11      66.91  
1       

KeyError: 'date_id'